In [2]:
from creds import HOST_NAME, DB_NAME, USERNAME , PASSWORD 
import pandas as pd
import duckdb as duck
import psycopg
import numpy as np
import warnings
warnings.filterwarnings("ignore")

def exec_query_os(query):
    conn = psycopg.connect(
        dbname=DB_NAME, user=USERNAME, password=PASSWORD, host=HOST_NAME, port="5432"
    )
    df = pd.read_sql(query, conn)

    conn.close()
    return df

def df_to_parquet(df, table_name):
    df.to_parquet(f"./data/{table_name}.parquet", compression='gzip')


## Reading NBA Data from db

In [29]:
game_box_df = exec_query_os("""
                SELECT *
                FROM public."NBA_GAME_BOX_HIST"
                where season = 2024;
            """)

game_pbp_df = exec_query_os("""
                SELECT *
                FROM public."NBA_PBP_HIST"
                where season = 2024;
            """)

player_box_df = exec_query_os("""
                SELECT *
                FROM public."NBA_PLAYER_BOX_HIST"
                where season = 2024;
            """)


In [4]:
print(game_box_df.shape)
print(game_pbp_df.shape)
print(player_box_df.shape)


(2628, 57)
(611682, 64)
(34867, 57)


## Cleaning and Normalizing Data

### Team Game Stats

In [5]:
team_schedules = game_box_df.copy()

# Creating a home away 'indicator' - mainly for tooltip
team_schedules['game_title'] = np.where(team_schedules['team_home_away'] == 'home',
                                      team_schedules['opponent_team_abbreviation'] + ' @ ' + team_schedules['team_abbreviation'],
                                      team_schedules['team_abbreviation'] + ' @ ' + team_schedules['opponent_team_abbreviation']
                                    )

# Creating win loss 'indicator' - mainly for tooltip
team_schedules['outcome_title'] = np.where(team_schedules['team_winner'] == True,
                                      'W ' + team_schedules['team_score'].astype(str) + '-' + team_schedules['opponent_team_score'].astype(str),
                                      'L ' + team_schedules['opponent_team_score'].astype(str) + '-' + team_schedules['team_score'].astype(str)
                                    )

print(team_schedules.shape)
team_schedules.head()

(2628, 59)


game_id  season  season_type   game_date            game_date_time  \
0  401656363    2024            3  2024-06-17 2024-06-18 00:30:00+00:00   
1  401656363    2024            3  2024-06-17 2024-06-18 00:30:00+00:00   
2  401656362    2024            3  2024-06-14 2024-06-15 00:30:00+00:00   
3  401656362    2024            3  2024-06-14 2024-06-15 00:30:00+00:00   
4  401656361    2024            3  2024-06-12 2024-06-13 00:30:00+00:00   

   team_id       team_uid         team_slug team_location  team_name  ...  \
0        6  s:40~l:46~t:6  dallas-mavericks        Dallas  Mavericks  ...   
1        2  s:40~l:46~t:2    boston-celtics        Boston    Celtics  ...   
2        2  s:40~l:46~t:2    boston-celtics        Boston    Celtics  ...   
3        6  s:40~l:46~t:6  dallas-mavericks        Dallas  Mavericks  ...   
4        2  s:40~l:46~t:2    boston-celtics        Boston    Celtics  ...   

  opponent_team_abbreviation opponent_team_display_name  \
0                        BOS             Boston Celtics   
1                        DAL           Dallas Mavericks   
2                        DAL           Dallas Mavericks   
3                        BOS             Boston Celtics   
4                        DAL           Dallas Mavericks   

  opponent_team_short_display_name opponent_team_color  \
0                          Celtics              008348   
1                        Mavericks              0064b1   
2                        Mavericks              0064b1   
3                          Celtics              008348   
4                        Mavericks              0064b1   

  opponent_team_alternate_color  \
0                        ffffff   
1                        bbc4ca   
2                        bbc4ca   
3                        ffffff   
4                        bbc4ca   

                                  opponent_team_logo opponent_team_score  \
0  https://a.espncdn.com/i/teamlogos/nba/500/bos.png                 106   
1  https://a.espncdn.com/i/teamlogos/nba/500/dal.png                  88   
2  https://a.espncdn.com/i/teamlogos/nba/500/dal.png                 122   
3  https://a.espncdn.com/i/teamlogos/nba/500/bos.png                  84   
4  https://a.espncdn.com/i/teamlogos/nba/500/dal.png                  99   

   largest_lead  game_title  outcome_title  
0             0   DAL @ BOS       L 106-88  
1            26   DAL @ BOS       W 106-88  
2             3   BOS @ DAL       L 122-84  
3            48   BOS @ DAL       W 122-84  
4            21   BOS @ DAL       W 106-99  

[5 rows x 59 columns]

In [ ]:
# normalizing team game dataframe
# 4 final dataframes

# splitting team info into separate table
team_lkp = team_schedules.copy()
team_lkp = team_lkp[['team_id', 'team_slug', 'team_location', 'team_name',
       'team_abbreviation', 'team_display_name', 'team_short_display_name',
       'team_color', 'team_alternate_color', 'team_logo']].drop_duplicates().reset_index(drop=True)

# splitting game outcome into separate table
game_overview = team_schedules.copy()
game_overview = game_overview[['game_id', 'season', 'season_type', 'game_date', 'game_date_time', 'game_title']].drop_duplicates().reset_index(drop=True)

# splitting home and away into separate table
home_stats = team_schedules.copy()
home_stats = home_stats[home_stats['team_home_away'] == 'home'][['game_id', 'team_id',
                                                               'team_score', 'team_winner', 'assists', 'blocks', 
                                                               'defensive_rebounds', 'fast_break_points', 'field_goal_pct', 
                                                               'field_goals_made', 'field_goals_attempted', 'flagrant_fouls', 
                                                               'fouls', 'free_throw_pct','free_throws_made', 'free_throws_attempted', 
                                                               'offensive_rebounds','points_in_paint', 'steals', 'team_turnovers', 
                                                               'technical_fouls','three_point_field_goal_pct', 'three_point_field_goals_made',
                                                               'three_point_field_goals_attempted', 'total_rebounds','total_technical_fouls', 
                                                               'total_turnovers', 'turnover_points', 'turnovers']].reset_index(drop=True)

away_stats = team_schedules.copy()
away_stats = away_stats[away_stats['team_home_away'] == 'away'][['game_id', 'team_id',
                                                               'team_score', 'team_winner', 'assists', 'blocks', 
                                                               'defensive_rebounds', 'fast_break_points', 'field_goal_pct', 
                                                               'field_goals_made', 'field_goals_attempted', 'flagrant_fouls', 
                                                               'fouls', 'free_throw_pct','free_throws_made', 'free_throws_attempted', 
                                                               'offensive_rebounds','points_in_paint', 'steals', 'team_turnovers', 
                                                               'technical_fouls','three_point_field_goal_pct', 'three_point_field_goals_made',
                                                               'three_point_field_goals_attempted', 'total_rebounds','total_technical_fouls', 
                                                               'total_turnovers', 'turnover_points', 'turnovers']].reset_index(drop=True)
# adding team id's to game overview table
final_game_overview = pd.merge(
       pd.merge(
              game_overview, home_stats[['game_id', 'team_id']], on='game_id', how='left'
       ).rename(columns={'team_id':'home_team_id'}),
       away_stats[['game_id', 'team_id']], on='game_id', how='left'
       ).rename(columns={'team_id':'away_team_id'}).reset_index(drop=True)

print(f"Team Lookup Table Shape: {team_lkp.shape}")
print(f"Game Overview Table Shape: {final_game_overview.shape}")
print(f"Home Team Stats Table Shape: {home_stats.shape}")
print(f"Away Team Stats Table Shape: {away_stats.shape}")

Team Lookup Table Shape: (32, 11)
Game Overview Table Shape: (1314, 8)
Home Team Stats Table Shape: (1314, 29)
Away Team Stats Table Shape: (1314, 29)


### Player Game Stats

In [7]:
# Creating a player info table
player_lkp = player_box_df.copy()
player_lkp = player_lkp[['athlete_id', 'athlete_display_name', 'athlete_headshot_href',
                               'athlete_position_name', 'athlete_position_abbreviation']].drop_duplicates().reset_index(drop=True)

# Creating a link to team
player_team_lkp = player_box_df.copy()
player_team_lkp = player_team_lkp[['athlete_id','team_id', 'game_date']].drop_duplicates()
player_team_lkp = player_team_lkp.groupby(['athlete_id','team_id'], as_index=False).agg({
                'game_date': ['min', 'max']
})
player_team_lkp.columns = ['athlete_id', 'team_id', 'first_game_date', 'last_game_date']
player_team_lkp = player_team_lkp.reset_index(drop=True)

# game player stat
player_game_stat= player_box_df.copy()
player_game_stat = player_game_stat[['game_id','athlete_id', 'minutes', 'field_goals_made', 'field_goals_attempted', 
                                     'three_point_field_goals_made', 'three_point_field_goals_attempted', 'free_throws_made',
                                     'free_throws_attempted', 'offensive_rebounds', 'defensive_rebounds', 'rebounds', 'assists',
                                     'steals', 'blocks', 'turnovers', 'fouls', 'plus_minus', 'points', 'starter', 'ejected',
                                     'did_not_play', 'active', 'reason']].drop_duplicates().reset_index(drop=True)

print(f"Player Lookup Table Shape: {player_lkp.shape}")
print(f"player Team Info Table Shape: {player_team_lkp.shape}")
print(f"Game Player Stats Table Shape: {player_game_stat.shape}")

Player Lookup Table Shape: (589, 5)
player Team Info Table Shape: (704, 4)
Game Player Stats Table Shape: (34867, 24)


### Play by Play Player Stats

In [31]:
# Normalizing player pbp data

# grouping by event types
type_1 = [7, 8, 9, 10, 11, 12, 13, 22, 24, 25, 28, 29, 30, 31, 32, 33, 35, 36, 37, 40, 42, 43, 44, 45, 46, 47, 48, 257]
type_2 = [16, 213, 214, 215, 216, 277, 278, 279, 280, 402, 412, 517, 584, 615]
type_3 = [61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 80, 81, 82, 84, 86, 87, 88, 90, 206]
type_4 = [91, 92, 93, 94, 95, 96, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125,
          126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147,
          148, 149, 150, 151, 152, 153]
type_5 = [97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 157, 165, 166]
type_6 = [155, 156]

game_pbp_frmt = game_pbp_df.copy()
game_pbp_frmt['period_id'] = game_pbp_frmt['game_id'].astype(str) + game_pbp_frmt['period_number'].astype(str)

type_group_conditions = [
            game_pbp_frmt['type_id'] == 0,
            game_pbp_frmt['type_id'].isin(type_1),
            game_pbp_frmt['type_id'].isin(type_2),
            game_pbp_frmt['type_id'].isin(type_3),
            game_pbp_frmt['type_id'].isin(type_4),
            game_pbp_frmt['type_id'].isin(type_5),
            game_pbp_frmt['type_id'].isin(type_6)
]
game_pbp_frmt['type_group_id'] = np.select(type_group_conditions, [0, 1, 2, 3, 4, 5, 6], default=0)

type_group_desc_conditions = [
            game_pbp_frmt['type_group_id'] == 0,
            game_pbp_frmt['type_group_id'] == 1,
            game_pbp_frmt['type_group_id'] == 2,
            game_pbp_frmt['type_group_id'] == 3,
            game_pbp_frmt['type_group_id'] == 4,
            game_pbp_frmt['type_group_id'] == 5,
            game_pbp_frmt['type_group_id'] == 6
]
type_group_descs = ['None', 'foul', 'pause', 'turnover', 'shot', 'free-throw', 'rebound']
game_pbp_frmt['type_group_text'] = np.select(type_group_desc_conditions, type_group_descs, default='None')

# game period lookup
game_period_lkp = game_pbp_frmt.copy()
game_period_lkp = game_period_lkp[['game_id', 'period_id', 'period_number']].drop_duplicates().sort_values(
                    by=['game_id', 'period_id'], ascending=True
                ).reset_index(drop=True)

# period time info lookup
period_time = game_pbp_frmt.copy()
period_time = period_time[['period_id', 'id', 'sequence_number', 'wallclock',
                           'clock_display_value', 'start_quarter_seconds_remaining', 'start_half_seconds_remaining',
                           'start_game_seconds_remaining', 'game_play_number', 'end_quarter_seconds_remaining', 'end_half_seconds_remaining',
                           'end_game_seconds_remaining']].drop_duplicates().reset_index(drop=True)

# game score lookup
game_score_lkp = game_pbp_frmt.copy()
game_score_lkp = game_score_lkp[['period_id', 'id', 'sequence_number',
                                 'home_score', 'away_score']].drop_duplicates().reset_index(drop=True)

# event type lookup
event_type_lkp = game_pbp_frmt.copy()
event_type_lkp = event_type_lkp[['type_group_id', 'type_group_text',
                                 'type_id', 'type_text']].drop_duplicates().reset_index(drop=True)

# play overview 
play_overview = game_pbp_frmt.copy()
play_overview = play_overview[['id', 'type_id', 'team_id', 'scoring_play', 'score_value', 'shooting_play',
                               'athlete_id_1', 'athlete_id_2', 'athlete_id_3', 'coordinate_x',
                               'coordinate_y']].drop_duplicates().reset_index(drop=True)

print(f"Game Period Lookup Table Shape: {game_period_lkp.shape}")
print(f"Period Time Info Table Shape: {period_time.shape}")
print(f"Game Score Lookup Table Shape: {game_score_lkp.shape}")
print(f"Event Type Lookup Table Shape: {event_type_lkp.shape}")
print(f"Player Play Stat Table Shape: {play_overview.shape}")

Game Period Lookup Table Shape: (5326, 3)
Period Time Info Table Shape: (611682, 12)
Game Score Lookup Table Shape: (611682, 5)
Event Type Lookup Table Shape: (138, 4)
Player Play Stat Table Shape: (611682, 11)


## Change Data Types and Export to parquet

In [60]:
# Adjusting data types according to ERD

GAME_PERIOD_LKP = game_period_lkp.copy()
GAME_PERIOD_LKP['period_id'] = GAME_PERIOD_LKP['period_id'].astype(int)

PERIOD_INFO_LKP = period_time.copy()
PERIOD_INFO_LKP['period_id'] = PERIOD_INFO_LKP['period_id'].astype(int)
PERIOD_INFO_LKP['id'] = PERIOD_INFO_LKP['id'].astype(int)
PERIOD_INFO_LKP['sequence_number'] = PERIOD_INFO_LKP['sequence_number'].astype(int)
PERIOD_INFO_LKP['wallclock'] = pd.to_datetime(PERIOD_INFO_LKP['wallclock'])
PERIOD_INFO_LKP['clock_display_value'] = PERIOD_INFO_LKP['clock_display_value'].astype(str)

GAME_PLAY_SCORE_LKP = game_score_lkp.copy()
GAME_PLAY_SCORE_LKP['period_id'] = GAME_PLAY_SCORE_LKP['period_id'].astype(int)
GAME_PLAY_SCORE_LKP['id'] = GAME_PLAY_SCORE_LKP['id'].astype(int)
GAME_PLAY_SCORE_LKP['sequence_number'] = GAME_PLAY_SCORE_LKP['sequence_number'].astype(int)

PLAY_TYPE_LKP = event_type_lkp.copy()
PLAY_TYPE_LKP['type_group_text'] = PLAY_TYPE_LKP['type_group_text'].astype(str)
PLAY_TYPE_LKP['type_text'] = PLAY_TYPE_LKP['type_text'].astype(str)

PLAY_INFO_OVERVIEW = play_overview.copy()
PLAY_INFO_OVERVIEW['id'] = PLAY_INFO_OVERVIEW['id'].astype(int)
PLAY_INFO_OVERVIEW['team_id'] = PLAY_INFO_OVERVIEW['team_id'].fillna(0)
PLAY_INFO_OVERVIEW['team_id'] = PLAY_INFO_OVERVIEW['team_id'].astype(int)

ATHLETE_INFO_LKP = player_lkp.copy()
ATHLETE_INFO_LKP['athlete_display_name'] = ATHLETE_INFO_LKP['athlete_display_name'].astype(str)
ATHLETE_INFO_LKP['athlete_position_name'] = ATHLETE_INFO_LKP['athlete_position_name'].astype(str)
ATHLETE_INFO_LKP['athlete_position_abbreviation'] = ATHLETE_INFO_LKP['athlete_position_abbreviation'].astype(str)

ATHLETE_ACTIVE_TEAM_LKP = player_team_lkp.copy()
ATHLETE_ACTIVE_TEAM_LKP['first_game_date'] = pd.to_datetime(ATHLETE_ACTIVE_TEAM_LKP['first_game_date'])
ATHLETE_ACTIVE_TEAM_LKP['first_game_date'] = ATHLETE_ACTIVE_TEAM_LKP['first_game_date'].dt.date
ATHLETE_ACTIVE_TEAM_LKP['last_game_date'] = pd.to_datetime(ATHLETE_ACTIVE_TEAM_LKP['last_game_date'])
ATHLETE_ACTIVE_TEAM_LKP['last_game_date'] = ATHLETE_ACTIVE_TEAM_LKP['last_game_date'].dt.date

PLAYER_GAME_STATS = player_game_stat.copy()
PLAYER_GAME_STATS['plus_minus'] = PLAYER_GAME_STATS['plus_minus'].astype(str)
PLAYER_GAME_STATS['reason'] = PLAYER_GAME_STATS['reason'].astype(str)

TEAM_INFO_LKP = team_lkp.copy()

GAME_INFO_OVERVIEW = final_game_overview.copy()
GAME_INFO_OVERVIEW['game_date'] =  pd.to_datetime(GAME_INFO_OVERVIEW['game_date'])
GAME_INFO_OVERVIEW['game_date'] =  GAME_INFO_OVERVIEW['game_date'].dt.date

GAME_INFO_OVERVIEW['game_date_time'] = pd.to_datetime(GAME_INFO_OVERVIEW['game_date'])

HOME_TEAM_GAME_STATS = home_stats.copy()
HOME_TEAM_GAME_STATS['fast_break_points'] = HOME_TEAM_GAME_STATS['fast_break_points'].astype(int)

AWAY_TEAM_GAME_STATS = away_stats.copy()
AWAY_TEAM_GAME_STATS['fast_break_points'] = AWAY_TEAM_GAME_STATS['fast_break_points'].astype(int)


In [65]:
# Sending tables to parquet files

GAME_PERIOD_LKP.to_parquet('./data/GAME_PERIOD_LKP.parquet', engine='pyarrow')
PERIOD_INFO_LKP.to_parquet('./data/PERIOD_INFO_LKP.parquet', engine='pyarrow')
GAME_PLAY_SCORE_LKP.to_parquet('./data/GAME_PLAY_SCORE_LKP.parquet', engine='pyarrow')
PLAY_TYPE_LKP.to_parquet('./data/PLAY_TYPE_LKP.parquet', engine='pyarrow')
PLAY_INFO_OVERVIEW.to_parquet('./data/PLAY_INFO_OVERVIEW.parquet', engine='pyarrow')
ATHLETE_INFO_LKP.to_parquet('./data/ATHLETE_INFO_LKP.parquet', engine='pyarrow')
ATHLETE_ACTIVE_TEAM_LKP.to_parquet('./data/ATHLETE_ACTIVE_TEAM_LKP.parquet', engine='pyarrow')
PLAYER_GAME_STATS.to_parquet('./data/PLAYER_GAME_STATS.parquet', engine='pyarrow')
TEAM_INFO_LKP.to_parquet('./data/TEAM_INFO_LKP.parquet', engine='pyarrow')
GAME_INFO_OVERVIEW.to_parquet('./data/GAME_INFO_OVERVIEW.parquet', engine='pyarrow')
HOME_TEAM_GAME_STATS.to_parquet('./data/HOME_TEAM_GAME_STATS.parquet', engine='pyarrow')
AWAY_TEAM_GAME_STATS.to_parquet('./data/AWAY_TEAM_GAME_STATS.parquet', engine='pyarrow')


## Testing Analysis and Visuals

In [ ]:
# duck.read_parquet('')
query = """
with q1 as (
    select a1.game_id
        , a1.home_team_id
        , a2.team_score as home_team_score
        , a2.team_winner as home_team_winner
        , a3.team_display_name as home_team_display_name
        , a3.team_logo as home_team_logo
    from './data/GAME_INFO_OVERVIEW.parquet' a1
    inner join './data/HOME_TEAM_GAME_STATS.parquet' a2
    on a1.game_id = a2.game_id and a1.home_team_id=a2.team_id
    left join './data/TEAM_INFO_LKP.parquet' a3
    on a1.home_team_id = a3.team_id
),

q2 as (
    select a1.game_id
        , a1.away_team_id
        , a2.team_score as away_team_score
        , a2.team_winner as away_team_winner
        , a3.team_display_name as away_team_display_name
        , a3.team_logo as away_team_logo
    from './data/GAME_INFO_OVERVIEW.parquet' a1
    inner join './data/AWAY_TEAM_GAME_STATS.parquet' a2
    on a1.game_id = a2.game_id and a1.away_team_id=a2.team_id
    left join './data/TEAM_INFO_LKP.parquet' a3
    on a1.away_team_id = a3.team_id
)

select
    t1.game_id
    , t1.game_date
    , t1.game_title
    , q1.home_team_id
    , q1.home_team_score
    , q1.home_team_winner
    , q1.home_team_display_name
    , q1.home_team_logo 
    , q2.away_team_id
    , q2.away_team_score
    , q2.away_team_winner
    , q2.away_team_display_name
    , q2.away_team_logo
from './data/GAME_INFO_OVERVIEW.parquet' t1
left join q1
on q1.game_id = t1.game_id
left join q2
on q2.game_id = t1.game_id

"""

# Execute query with DuckDB
game_matchup_view = duck.query(query).df()

print(game_matchup_view.shape)
game_matchup_view.head()

(1314, 13)


game_id  game_date game_title  home_team_id  home_team_score  \
0  401656363 2024-06-17  DAL @ BOS             2              106   
1  401656359 2024-06-06  DAL @ BOS             2              107   
2  401585475 2024-02-28  SAC @ DEN             7              117   
3  401585432 2024-02-23  TOR @ ATL             1              121   
4  401585249 2024-01-24  MEM @ MIA            14               96   

   home_team_winner home_team_display_name  \
0              True         Boston Celtics   
1              True         Boston Celtics   
2              True         Denver Nuggets   
3             False          Atlanta Hawks   
4             False             Miami Heat   

                                      home_team_logo  away_team_id  \
0  https://a.espncdn.com/i/teamlogos/nba/500/bos.png             6   
1  https://a.espncdn.com/i/teamlogos/nba/500/bos.png             6   
2  https://a.espncdn.com/i/teamlogos/nba/500/den.png            23   
3  https://a.espncdn.com/i/teamlogos/nba/500/atl.png            28   
4  https://a.espncdn.com/i/teamlogos/nba/500/mia.png            29   

   away_team_score  away_team_winner away_team_display_name  \
0               88             False       Dallas Mavericks   
1               89             False       Dallas Mavericks   
2               96             False       Sacramento Kings   
3              123              True        Toronto Raptors   
4              105              True      Memphis Grizzlies   

                                      away_team_logo  
0  https://a.espncdn.com/i/teamlogos/nba/500/dal.png  
1  https://a.espncdn.com/i/teamlogos/nba/500/dal.png  
2  https://a.espncdn.com/i/teamlogos/nba/500/sac.png  
3  https://a.espncdn.com/i/teamlogos/nba/500/tor.png  
4  https://a.espncdn.com/i/teamlogos/nba/500/mem.png

In [83]:
query = """
with q1 as (
    select *
    from './data/HOME_TEAM_GAME_STATS.parquet'
    UNION
    select *
    from './data/AWAY_TEAM_GAME_STATS.parquet'
)
select q1.*
    , a1.team_display_name
    , a2.game_date
from q1
left join './data/TEAM_INFO_LKP.parquet' a1
on q1.team_id = a1.team_id
left join './data/GAME_INFO_OVERVIEW.parquet' a2
on q1.game_id = a2.game_id
order by q1.game_id
"""

# Can then use these to calculate averages, other stats
team_game_stats_view = duck.query(query).df()

print(team_game_stats_view.shape)
team_game_stats_view.head()

(2628, 31)


game_id  team_id  team_score  team_winner  assists  blocks  \
0  401584089       11         121         True       28       5   
1  401584089        5         116        False       27       9   
2  401584090       15         110         True       24      11   
3  401584090       18         105        False       18       1   
4  401584091       27         114        False       33       4   

   defensive_rebounds  fast_break_points  field_goal_pct  field_goals_made  \
0                  33                 17            52.3                45   
1                  30                 24            52.4                44   
2                  34                  7            42.7                35   
3                  40                 15            39.6                38   
4                  26                 22            56.8                46   

   ...  three_point_field_goal_pct  three_point_field_goals_made  \
0  ...                        48.4                            15   
1  ...                        28.6                             8   
2  ...                        51.3                            20   
3  ...                        25.6                            10   
4  ...                        46.4                            13   

   three_point_field_goals_attempted  total_rebounds  total_technical_fouls  \
0                                 31              40                      0   
1                                 28              35                      3   
2                                 39              41                      2   
3                                 39              56                      1   
4                                 28              30                      0   

   total_turnovers  turnover_points turnovers    team_display_name  game_date  
0               19               26        18       Indiana Pacers 2023-11-03  
1               13               15        13  Cleveland Cavaliers 2023-11-03  
2               14               14        14      Milwaukee Bucks 2023-11-03  
3               11                4        10      New York Knicks 2023-11-03  
4               20               17        20   Washington Wizards 2023-11-03  

[5 rows x 31 columns]

In [3]:
query = """
with sub as (
    select q1.*
        , a1.game_title
        , a1.game_date
        , a2.athlete_display_name
        , a2.athlete_headshot_href
    from './data/PLAYER_GAME_STATS.parquet' q1
    left join './data/GAME_INFO_OVERVIEW.parquet' a1
    on q1.game_id = a1.game_id
    left join './data/ATHLETE_INFO_LKP.parquet' a2
    on q1.athlete_id = a2.athlete_id
    order by q1.game_id
),

sub2 as (
select sub.*
    , t1.team_id
    , t1.first_game_date
    , t1.last_game_date
from sub
left join './data/ATHLETE_ACTIVE_TEAM_LKP.parquet' t1
on sub.athlete_id = t1.athlete_id
),

sub3 as (
    select sub2.*
    , case when sub2.game_date between sub2.first_game_date and sub2.last_game_date then sub2.team_id
    else null end as active_team_id
    from sub2
),

sub4 as (
    select sub3.*
    from sub3
    where sub3.active_team_id is not null
)

select sub4.*
    , l1.team_display_name
from sub4
left join './data/TEAM_INFO_LKP.parquet' l1
on sub4.active_team_id = l1.team_id
"""

# getting player game stats with active team
player_game_stats_view = duck.query(query).df()

print(player_game_stats_view.shape)
player_game_stats_view.head()

(34891, 33)


game_id  athlete_id  minutes  field_goals_made  field_goals_attempted  \
0  401584089     4066328     21.0               4.0                    6.0   
1  401584089     4396907     32.0               5.0                   11.0   
2  401584089     4065778     28.0               4.0                    9.0   
3  401584089     3912848      3.0               0.0                    0.0   
4  401584089     2990969     27.0               4.0                    9.0   

   three_point_field_goals_made  three_point_field_goals_attempted  \
0                           0.0                                0.0   
1                           0.0                                2.0   
2                           1.0                                6.0   
3                           0.0                                0.0   
4                           2.0                                6.0   

   free_throws_made  free_throws_attempted  offensive_rebounds  ...  \
0               2.0                    3.0                 2.0  ...   
1               4.0                    4.0                 0.0  ...   
2               1.0                    2.0                 0.0  ...   
3               0.0                    0.0                 0.0  ...   
4               2.0                    2.0                 0.0  ...   

             reason  game_title  game_date  athlete_display_name  \
0  COACH'S DECISION   CLE @ IND 2023-11-03         Jarrett Allen   
1  COACH'S DECISION   CLE @ IND 2023-11-03        Darius Garland   
2  COACH'S DECISION   CLE @ IND 2023-11-03             Max Strus   
3  COACH'S DECISION   CLE @ IND 2023-11-03             Dean Wade   
4  COACH'S DECISION   CLE @ IND 2023-11-03         Georges Niang   

                               athlete_headshot_href  team_id  \
0  https://a.espncdn.com/i/headshots/nba/players/...        5   
1  https://a.espncdn.com/i/headshots/nba/players/...        5   
2  https://a.espncdn.com/i/headshots/nba/players/...        5   
3  https://a.espncdn.com/i/headshots/nba/players/...        5   
4  https://a.espncdn.com/i/headshots/nba/players/...        5   

   first_game_date last_game_date  active_team_id    team_display_name  
0       2023-11-03     2024-05-15               5  Cleveland Cavaliers  
1       2023-10-25     2024-05-15               5  Cleveland Cavaliers  
2       2023-10-25     2024-05-15               5  Cleveland Cavaliers  
3       2023-10-27     2024-05-15               5  Cleveland Cavaliers  
4       2023-10-25     2024-05-15               5  Cleveland Cavaliers  

[5 rows x 33 columns]

In [7]:
query = """
with q1 as (
    select sub.* 
        , sub2.clock_display_value
        , sub2.id
        , sub3.game_date
        , sub3.game_title
    from './data/GAME_PERIOD_LKP.parquet' sub
    left join './data/PERIOD_INFO_LKP.parquet' sub2
    on sub.period_id = sub2.period_id
    left join './data/GAME_INFO_OVERVIEW.parquet' sub3
    on sub.game_id = sub3.game_id
)

select t1.id
    , t1.type_id
    , t1.team_id
    , l1.type_text
    , l1.type_group_text
    , t1.scoring_play
    , t1.score_value
    , t1.athlete_id_1
    , t1.coordinate_x
    , t1.coordinate_y
    , a2.athlete_display_name
    , q1.clock_display_value
    , q1.game_date
    , q1.game_title
    , q1.period_number
from './data/PLAY_INFO_OVERVIEW.parquet' t1
left join './data/ATHLETE_INFO_LKP.parquet' a2
on t1.athlete_id_1 = a2.athlete_id
left join q1
on t1.id = q1.id
left join './data/PLAY_TYPE_LKP.parquet' l1
on t1.type_id = l1.type_id
where t1.shooting_play = True
and l1.type_group_text not in ('free-throw')
"""

# Can then use these to calculate averages, other stats
shooting_chart_view = duck.query(query).df()

print(shooting_chart_view.shape)
shooting_chart_view.head()

(232999, 15)


id  type_id  team_id                  type_text type_group_text  \
0  401585680297       95       12                 Layup Shot            shot   
1  401585680300      131       20           Pullup Jump Shot            shot   
2  401585680311      131       20           Pullup Jump Shot            shot   
3   40158568354       92       29                  Jump Shot            shot   
4   40158568356      129       13  Running Finger Roll Layup            shot   

   scoring_play  score_value  athlete_id_1  coordinate_x  coordinate_y  \
0         False            0     4017837.0        -38.75           3.0   
1         False            0     4431678.0         34.75          16.0   
2         False            0        3012.0         19.75         -16.0   
3         False            0     5105550.0         41.75          23.0   
4          True            2        1966.0        -40.75           0.0   

  athlete_display_name clock_display_value  game_date game_title  \
0          Ivica Zubac                1:05 2024-03-27  LAC @ PHI   
1         Tyrese Maxey              0:54.1 2024-03-27  LAC @ PHI   
2           Kyle Lowry              0:26.0 2024-03-27  LAC @ PHI   
3        GG Jackson II                8:00 2024-03-27  LAL @ MEM   
4         LeBron James                7:54 2024-03-27  LAL @ MEM   

   period_number  
0              2  
1              2  
2              2  
3              1  
4              1

### Shot Chart

In [8]:
testing_chart = shooting_chart_view.copy()
testing_chart = testing_chart[testing_chart['athlete_display_name'] == 'Luka Doncic'].reset_index(drop=True)
testing_chart['quarter_time_clock'] = "Quarter " + testing_chart['period_number'].astype(str) + " - " + testing_chart['clock_display_value'].astype(str)
testing_chart['game_date_frmt'] = testing_chart['game_date'].dt.strftime('%B %d, %Y')

testing_chart.head()

id  type_id  team_id                   type_text type_group_text  \
0  401585499377      114        6        Turnaround Jump Shot            shot   
1   40165636344      144        6  Driving Floating Jump Shot            shot   
2   40165636368      131        6            Pullup Jump Shot            shot   
3  401656363120      131        6            Pullup Jump Shot            shot   
4  401656363112      121        6         Fade Away Jump Shot            shot   

   scoring_play  score_value  athlete_id_1  coordinate_x  coordinate_y  \
0         False            0     3945274.0         32.75           0.0   
1         False            0     3945274.0        -31.75           6.0   
2          True            2     3945274.0        -34.75           2.0   
3         False            0     3945274.0        -23.75           1.0   
4          True            2     3945274.0        -25.75         -11.0   

  athlete_display_name clock_display_value  game_date game_title  \
0          Luka Doncic                8:30 2024-03-03  PHI @ DAL   
1          Luka Doncic                8:12 2024-06-17  DAL @ BOS   
2          Luka Doncic                7:02 2024-06-17  DAL @ BOS   
3          Luka Doncic                2:53 2024-06-17  DAL @ BOS   
4          Luka Doncic                3:23 2024-06-17  DAL @ BOS   

   period_number quarter_time_clock  game_date_frmt  
0              3   Quarter 3 - 8:30  March 03, 2024  
1              1   Quarter 1 - 8:12   June 17, 2024  
2              1   Quarter 1 - 7:02   June 17, 2024  
3              1   Quarter 1 - 2:53   June 17, 2024  
4              1   Quarter 1 - 3:23   June 17, 2024

In [9]:
import plotly.graph_objects as go

fig = go.Figure()

fig.add_trace(
    go.Scatter(x=testing_chart['coordinate_x'],
                            y=testing_chart['coordinate_y'],
                            mode='markers',
                            marker=dict(
                                line=dict(width=2, color='DarkSlateGrey'),
                                symbol=[ 'circle' if x > 0 else 'x' for x in testing_chart['score_value']],
                                color='#FB4141',
                                size=8,
                            ),
                            text=testing_chart['score_value'],
                            customdata=testing_chart[['game_date_frmt', 'game_title', 'quarter_time_clock', 'score_value', 'type_text']],
                            hovertemplate = '<b>Game Date:</b> %{customdata[0]}<br>' + 
                            '<b>Game Title: </b>%{customdata[1]}<br>' 
                            + '<b>Shot Time:</b> %{customdata[2]}<br>'
                            + '<b>Shot Points:</b> %{customdata[3]}<br>'
                            + '<b>Shot Type:</b> %{customdata[4]}<br> <extra></extra>' 
                            ))


fig.add_layout_image(
        dict(
            source="./data/court.jpg",
            x=0,
            y=1,
            xref="paper",
            yref="paper",
            sizex=1,
            sizey=1,
            xanchor="left",
            yanchor="top",
            sizing="stretch",
            layer="below" )
)


fig.update_yaxes(visible=False, showticklabels=False)
fig.update_xaxes(visible=False, showticklabels=False)


# Set templates

fig.update_layout(
                plot_bgcolor='#111111',
                template='plotly_dark',
                hoverlabel=dict(
                    bgcolor="white",
                    font_size=16,
                    font_family="Courier New, monospace"
                ),
                margin=dict(l=20, r=20, t=60, b=20),
                font=dict(family="Courier New, monospace"),
                xaxis=dict(zeroline=False, showgrid=False),
                yaxis=dict(zeroline=False, showgrid=False),)

fig.show(config={'displayModeBar': False, 'doubleClickDelay': 1000})

### Roster Lookup Chart

In [10]:
# 401585475

roster_chart = player_game_stats_view.copy()
roster_chart = roster_chart[(roster_chart['game_id'] == 401585475) &
                            (roster_chart['team_display_name'] == 'Sacramento Kings') & 
                            (roster_chart['did_not_play'] == False)].reset_index(drop=True)
roster_chart['plus_minus_frmt'] = pd.to_numeric(roster_chart['plus_minus'], errors='coerce').astype('Int64')
roster_chart['game_date_frmt'] = roster_chart['game_date'].dt.strftime('%B %d, %Y')

roster_chart['fg_frmt'] = ((((roster_chart['field_goals_made'] / roster_chart['field_goals_attempted'])*100).round(0)).astype(int)).astype(str) \
                        + "%  (" + roster_chart['field_goals_made'].astype(int).astype(str) + "/" + roster_chart['field_goals_attempted'].astype(int).astype(str) + ")"


roster_chart['3fg_frmt'] = roster_chart.apply(
                                        lambda x: str(int((x['three_point_field_goals_made'] / x['three_point_field_goals_attempted'])*100)) + \
                                            "%  (" + str(int(x['three_point_field_goals_made'])) + "/" + str(int(x['three_point_field_goals_attempted'])) + \
                                            ")" if x['three_point_field_goals_attempted'] > 0 else "0%", axis=1
                                        )

roster_chart['ft_frmt'] = roster_chart.apply(
                                        lambda x: str(int((x['free_throws_made'] / x['free_throws_attempted'])*100)) + \
                                            "%  (" + str(int(x['free_throws_made'])) + "/" + str(int(x['free_throws_attempted'])) + \
                                            ")" if x['free_throws_attempted'] > 0 else "0%", axis=1
                                        )

print(roster_chart.shape)
roster_chart.head()

(12, 38)


game_id  athlete_id  minutes  field_goals_made  field_goals_attempted  \
0  401585475     3155942     32.0               5.0                   14.0   
1  401585475        6578     20.0               2.0                    6.0   
2  401585475     4594327     33.0               9.0                   17.0   
3  401585475     4278053     16.0               2.0                    5.0   
4  401585475     4066372     18.0               2.0                    5.0   

   three_point_field_goals_made  three_point_field_goals_attempted  \
0                           0.0                                1.0   
1                           1.0                                4.0   
2                           3.0                                7.0   
3                           1.0                                3.0   
4                           0.0                                2.0   

   free_throws_made  free_throws_attempted  offensive_rebounds  ...  team_id  \
0               3.0                    4.0                 5.0  ...       23   
1               2.0                    2.0                 1.0  ...       23   
2               0.0                    0.0                 2.0  ...       23   
3               0.0                    0.0                 0.0  ...       23   
4               0.0                    2.0                 0.0  ...       23   

   first_game_date  last_game_date  active_team_id  team_display_name  \
0       2023-10-25      2024-04-14              23   Sacramento Kings   
1       2023-10-25      2024-04-14              23   Sacramento Kings   
2       2023-10-25      2024-04-14              23   Sacramento Kings   
3       2023-10-25      2024-04-14              23   Sacramento Kings   
4       2023-10-25      2024-03-18              23   Sacramento Kings   

   plus_minus_frmt     game_date_frmt      fg_frmt    3fg_frmt      ft_frmt  
0              -26  February 28, 2024  36%  (5/14)   0%  (0/1)   75%  (3/4)  
1              -21  February 28, 2024   33%  (2/6)  25%  (1/4)  100%  (2/2)  
2              -22  February 28, 2024  53%  (9/17)  42%  (3/7)           0%  
3              -11  February 28, 2024   40%  (2/5)  33%  (1/3)           0%  
4              -20  February 28, 2024   40%  (2/5)   0%  (0/2)    0%  (0/2)  

[5 rows x 38 columns]

In [120]:
roster_chart.columns

Index(['game_id', 'athlete_id', 'minutes', 'field_goals_made',
       'field_goals_attempted', 'three_point_field_goals_made',
       'three_point_field_goals_attempted', 'free_throws_made',
       'free_throws_attempted', 'offensive_rebounds', 'defensive_rebounds',
       'rebounds', 'assists', 'steals', 'blocks', 'turnovers', 'fouls',
       'plus_minus', 'points', 'starter', 'ejected', 'did_not_play', 'active',
       'reason', 'game_title', 'game_date', 'athlete_display_name',
       'athlete_headshot_href', 'team_id', 'first_game_date', 'last_game_date',
       'active_team_id', 'team_display_name', 'plus_minus_frmt',
       'game_date_frmt', 'fg_frmt', '3fg_frmt', 'ft_frmt'],
      dtype='object')

In [75]:
import urllib.request
from io import BytesIO 
from PIL import Image
import io
import base64


fig = go.Figure()

fig.add_trace(
    go.Scatter(x=roster_chart['minutes'],
                            y=roster_chart['plus_minus_frmt'],
                            mode='markers',
                            marker=dict(
                                line=dict(width=2, color='DarkSlateGrey'),
                                # symbol=[ 'circle' if x > 0 else 'x' for x in roster_chart['score_value']],
                                color='#FB4141',
                                size=8,
                                opacity=0
                            ),
                            customdata=roster_chart[['athlete_display_name', 'minutes', 'fg_frmt', '3fg_frmt', 'ft_frmt', 
                                                    'rebounds', 'assists',
                                                    'steals', 'blocks', 'turnovers', 'fouls', 'plus_minus', 'points',
                                                    'starter']],
                            hovertemplate = '<b>Player Name: </b>%{customdata[0]}<br>' 
                            + '<b>Minutes Played: </b>%{customdata[1]}<br>' 
                            + '<b>FG %:</b> %{customdata[2]}<br>'
                            + '<b>3-PT FG %:</b> %{customdata[3]}<br>'
                            + '<b>Free-Throw %:</b> %{customdata[4]}<br>'
                            + '<b>Rebounds:</b> %{customdata[5]}<br>'
                            + '<b>Assists:</b> %{customdata[6]}<br>'
                            + '<b>Steals:</b> %{customdata[7]}<br>'
                            + '<b>Blocks:</b> %{customdata[8]}<br>'
                            + '<b>Turnovers:</b> %{customdata[9]}<br>'
                            + '<b>Fouls:</b> %{customdata[10]}<br>'
                            + '<b>Plus-Minus:</b> %{customdata[11]}<br>'
                            + '<b>Total Points:</b> %{customdata[12]}<br>'
                            + '<b>Starter?:</b> %{customdata[13]}<br> <extra></extra>' 
                            ))

for t in roster_chart["athlete_display_name"].unique():
    url = roster_chart.loc[roster_chart['athlete_display_name']== f"{t}", "athlete_headshot_href"].values[0]
    # Opening image
    img = Image.open(BytesIO(urllib.request.urlopen(url).read())) 

    buffer = io.BytesIO()
    img.save(buffer, format="PNG")
    encoded_image = base64.b64encode(buffer.getvalue()).decode("utf-8")
    data_uri = f"data:image/png;base64,{encoded_image}"

    fig.add_layout_image(
        dict(
        source=data_uri,
        sizex=9,
        sizey=9,
        name=t,
        xref="x",
        yref="y",
        x=int(roster_chart.loc[roster_chart['athlete_display_name']== f"{t}", "minutes"].values[0]),
        y=int(roster_chart.loc[roster_chart['athlete_display_name']== f"{t}", "plus_minus_frmt"].values[0]),
        layer="above",
        opacity=.8, 
        xanchor="center",
        yanchor="middle",
        sizing="contain"
    ))

    # fig.add_shape(
    #     type="circle",
    #     x0=int(roster_chart.loc[roster_chart['athlete_display_name']== f"{t}", "minutes"].values[0]) - 1, 
    #     x1=int(roster_chart.loc[roster_chart['athlete_display_name']== f"{t}", "minutes"].values[0]) + 1,
    #     y0=int(roster_chart.loc[roster_chart['athlete_display_name']== f"{t}", "plus_minus_frmt"].values[0]) - 6.5,
    #     y1=int(roster_chart.loc[roster_chart['athlete_display_name']== f"{t}", "plus_minus_frmt"].values[0]) + 4,
    #     xref="x",
    #     yref="y",
    #     line=dict(color="white", width=2),
    #     fillcolor="#419197",
    # )

fig.update_shapes(opacity=0.2)

fig.update_layout(
                plot_bgcolor='#111111',
                template='plotly_dark',
                hoverlabel=dict(
                    bgcolor="white",
                    font_size=16,
                    font_family="Courier New, monospace"
                ),
                margin=dict(l=20, r=20, t=60, b=20),
                font=dict(family="Courier New, monospace"),
                xaxis_title='Minutes Played',
                yaxis_title='Plus-Minus',
                xaxis=dict(zeroline=True, showgrid=False),
                yaxis=dict(zeroline=True, showgrid=False),
                yaxis_range=[int(roster_chart['plus_minus_frmt'].min())-10, int(roster_chart['plus_minus_frmt'].max())+10],
                )


fig.show(config={'displayModeBar': False, 'doubleClickDelay': 1000})

### Moving Average

In [79]:
def calculate_moving_average(data, window_size):
    df = pd.DataFrame(data, columns=['Actual'])
    moving_average = df['Actual'].rolling(window=window_size).mean()
    return moving_average

In [88]:
def mov_avg_game(player_name, df, attr):
    init_df = df.sort_values(['athlete_display_name', 'game_date']).reset_index(drop=True)
    fltr_data = init_df[init_df['athlete_display_name']==player_name].reset_index(drop=True)

    data_points = fltr_data[attr].values.tolist()
    moving_avg_3_days = calculate_moving_average(data_points, window_size=3)
    moving_avg_5_days = calculate_moving_average(data_points, window_size=5)
    moving_avg_7_days = calculate_moving_average(data_points, window_size=7)

    fltr_data['mov_avg_3_gms'] = moving_avg_3_days
    fltr_data['mov_avg_5_gms'] = moving_avg_5_days
    fltr_data['mov_avg_7_gms'] = moving_avg_7_days

    actual_dp = fltr_data[attr].values.tolist()
    moving_avg_3= fltr_data["mov_avg_3_gms"].values.tolist()
    moving_avg_5 = fltr_data["mov_avg_5_gms"].values.tolist()
    moving_avg_7 = fltr_data["mov_avg_7_gms"].values.tolist()

    fig = go.Figure()

    # Add trace for actual points
    fig.add_trace(go.Scatter(x=list(range(1, len(actual_dp)+1))
                            , y=actual_dp, mode='lines+markers', name='Actual Points'
                            # , text=text_points
                            , marker=dict(
                                color='#419197',
                                size=5,
                                # angleref="previous"
                            ),
                            customdata=fltr_data[['game_date', 'game_title']],
                            hovertemplate = '<b>Game Date:</b> %{customdata[0]}<br>' + 
                            '<b>Game Matchup: </b>%{customdata[1]}<br>' + '<b>Attribute:</b> %{y}<br>'
                            ))

    # Add trace for moving average
    fig.add_trace(go.Scatter(x=list(range(1, len(moving_avg_3)+1))
                            , y=moving_avg_3, mode='lines', name='3-Game Moving Average'
                            , marker=dict(
                                color='#FF1E1E'
                            ),
                            hovertemplate = '<b>3-GM MA:</b> %{y}<br>'))

    fig.add_trace(go.Scatter(x=list(range(1, len(moving_avg_5)+1))
                            , y=moving_avg_5, mode='lines', name='5-Game Moving Average'
                            , marker=dict(
                                color='#06D001'
                            ),
                            hovertemplate = '<b>5-GM MA:</b> %{y}<br>'))

    fig.add_trace(go.Scatter(x=list(range(1, len(moving_avg_7)+1))
                            , y=moving_avg_7, mode='lines', name='7-Game Moving Average'
                            , marker=dict(
                                color='#FDFF00'
                            ),
                            hovertemplate = '<b>7-GM MA:</b> %{y}<br>'))

    fig.update_annotations(font_size=9, bordercolor='#419197', font_family="Courier New, monospace", font_color='black', borderwidth=1.5, borderpad=1.5, bgcolor='white')

    # Update layout
    fig.update_layout(
                    title=dict(
                        text="Game Trends",
                        xanchor='left',
                        yanchor='top'     
                    ),
                    xaxis_title='Game number',
                    yaxis_title=attr,
                    plot_bgcolor='#111111',
                    template='plotly_dark',
                    hoverlabel=dict(
                    bgcolor="white",
                    font_size=16,
                    font_family="Courier New, monospace"),
                    margin=dict(l=20, r=20, t=60, b=20),
                    font=dict(family="Courier New, monospace"))

    fig.update_yaxes(showline=False, gridcolor='#7D7C7C', griddash='dash', showspikes=True)
    fig.update_xaxes(showline=False, gridcolor='#7D7C7C', griddash='dash')
    # Show the figure
    # fig.show(config={'displayModeBar': False, 'doubleClickDelay': 1000})

    return fig

In [87]:
ma_attr_chart = player_game_stats_view.copy()
ma_attr_chart = ma_attr_chart[(ma_attr_chart['athlete_display_name'] == 'Luka Doncic') & 
                            (ma_attr_chart['did_not_play'] == False)].reset_index(drop=True)


ma_attr_chart.head()

game_id  athlete_id  minutes  field_goals_made  field_goals_attempted  \
0  401584094     3945274     38.0              11.0                   24.0   
1  401584102     3945274     32.0              17.0                   21.0   
2  401584110     3945274     26.0               5.0                   16.0   
3  401584147     3945274     38.0              15.0                   29.0   
4  401584701     3945274     34.0              13.0                   25.0   

   three_point_field_goals_made  three_point_field_goals_attempted  \
0                           6.0                               11.0   
1                           6.0                                9.0   
2                           3.0                                5.0   
3                           3.0                               10.0   
4                           3.0                               11.0   

   free_throws_made  free_throws_attempted  offensive_rebounds  ...  \
0               6.0                    7.0                 3.0  ...   
1               4.0                    4.0                 0.0  ...   
2               3.0                    5.0                 1.0  ...   
3               8.0                    9.0                 0.0  ...   
4               4.0                    7.0                 1.0  ...   

             reason  game_title  game_date  athlete_display_name  \
0  COACH'S DECISION   DAL @ DEN 2023-11-03           Luka Doncic   
1  COACH'S DECISION   LAC @ DAL 2023-11-10           Luka Doncic   
2  COACH'S DECISION    DAL @ NO 2023-11-14           Luka Doncic   
3  COACH'S DECISION   HOU @ DAL 2023-11-28           Luka Doncic   
4  COACH'S DECISION    DAL @ SA 2023-10-25           Luka Doncic   

                               athlete_headshot_href  team_id  \
0  https://a.espncdn.com/i/headshots/nba/players/...        6   
1  https://a.espncdn.com/i/headshots/nba/players/...        6   
2  https://a.espncdn.com/i/headshots/nba/players/...        6   
3  https://a.espncdn.com/i/headshots/nba/players/...        6   
4  https://a.espncdn.com/i/headshots/nba/players/...        6   

   first_game_date last_game_date  active_team_id  team_display_name  
0       2023-10-25     2024-06-17               6   Dallas Mavericks  
1       2023-10-25     2024-06-17               6   Dallas Mavericks  
2       2023-10-25     2024-06-17               6   Dallas Mavericks  
3       2023-10-25     2024-06-17               6   Dallas Mavericks  
4       2023-10-25     2024-06-17               6   Dallas Mavericks  

[5 rows x 33 columns]

In [90]:
mov_avg_game('Luka Doncic', ma_attr_chart, 'points')